## Import data

We will qury data from NOMAD to do the anlaysis on the fly. Here we have a couple of helper funcitions that help us doing the job. 

In [149]:
from pepe_plotly_theme import register_template, scatter_plot, set_defaults   

register_template()
set_defaults()

In [125]:
import re
import requests
import pandas as pd
import jmespath

from dotenv import load_dotenv
load_dotenv()  # this will read .env and set variables

URL = "https://nomad-lab.eu/prod/v1/staging/api/v1/entries/query"
INDEX_RE = re.compile(r"\[[^\]]*\]")

def normalize_quantity(q: str) -> str:
    """Remove any '#Section' suffix from a requested quantity."""
    return q.split("#", 1)[0]

def quantity_for_required(q: str) -> set[str]:
    """Keep section suffixes, drop only bracket indices."""
    if "#" in q:
        base, suffix = q.split("#", 1)
        suffix = f"#{suffix}"
    else:
        base, suffix = q, ""
    base = INDEX_RE.sub("", base)
    return {base + suffix}

def scalarize(val):
    """Turn lists/tuples/sets into a scalar (first element) when sensible."""
    if isinstance(val, (list, tuple, set)):
        return next(iter(val), None)
    return val

def dotted_get(d, path):
    """Fallback dotted getter for 'a.b.c' paths."""
    cur = d
    for key in path.split("."):
        if isinstance(cur, list):
            cur = cur[0] if cur else None
        if not isinstance(cur, dict):
            return None
        cur = cur.get(key)
        if cur is None:
            return None
    return scalarize(cur)

def jmes_get(d, expr):
    """Get with JMESPath if available; else fallback to dotted_get."""
    if jmespath:
        try:
            return scalarize(jmespath.search(expr, d))
        except Exception:
            return dotted_get(d, expr)
    return dotted_get(d, expr)

def post(query):
    r = requests.post(URL, json=query, timeout=60)
    if r.status_code == 422:
        try:
            payload = r.json()
        except ValueError:
            payload = r.text
        raise requests.HTTPError(
            f"422 from NOMAD. Request was rejected with: {payload}",
            response=r
        )
    r.raise_for_status()
    return r.json()

def fetch_all(base_query):
    q = {
        **base_query,
        "query": dict(base_query.get("query", {})),
        "pagination": dict(base_query.get("pagination", {})),
        "required": dict(base_query.get("required", {})),
    }
    items = []
    while True:
        resp = post(q)
        items.extend(resp.get("data", []))
        nxt = resp.get("pagination", {}).get("next_page_after_value")
        if not nxt:
            break
        q["pagination"]["page_after_value"] = nxt
    return items

def fetch_dataframe(quantities, page_size=1000, order="asc", order_by="entry_id"):
    """
    quantities: list of NOMAD quantity paths (may contain indices and/or '#Section' suffix)
    -> DataFrame with one column per requested quantity (normalized header)
    """
    include = sorted({
        inc for q in quantities for inc in quantity_for_required(q)
    })
    base_query = {
        "owner": "visible",
        "query": {
            "and": [
                {},
                {
                    "section_defs.definition_qualified_name:all": [
                        "perovskite_solar_cell_database.schema.PerovskiteSolarCell",
                        # "perovskite_solar_cell_database.composition.PerovskiteAIon",
                    ]
                }
            ]
        },
        "pagination": {"page_size": page_size, "order": order, "order_by": order_by},
        "required": {"include": include},
    }

    records = fetch_all(base_query)
    norm_paths = {q: normalize_quantity(q) for q in quantities}

    rows = []
    for item in records:
        row = {}
        for original_q, norm_q in norm_paths.items():
            if norm_q == "entry_id":
                row[original_q] = item.get("entry_id")
            else:
                row[original_q] = jmes_get(item, norm_q)   # use the suffix-free path here
        rows.append(row)


    rename_cols = {q: norm_paths[q] for q in quantities}
    df = pd.DataFrame(rows).rename(columns=rename_cols)
    return df

# --- Example usage ---
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "results.properties.electronic.band_gap[0].value",
]

df = fetch_dataframe(
    quantities=quantities,
    page_size=10000
)

df


entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
1      --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2      --9aa7m8b7HiItY8dhvSOhYziIQL   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
...                             ...   
43101  zzWmvvMCjbgxrnv6lvDISU7jQnDJ   
43102  zzZw_wGNpfUjQTtHnuNTSLZ_qG8s   
43103  zzdMGwagDZsgwpm8rCyYpDBkdOnR   
43104  zzo4cqAqKXO34NtM9ZItcLbh302O   
43105  zzsi9PLwayzu6t_th5OYrfmZsCIJ   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
1                                                  0.960                   
2                                                  0.632                   
3                                                  0.912                   
4                                                  0.885                   
...                                                  ...                   
43101                                              0.970                   
43102                                              0.981                   
43103                                              0.910                   
43104                                              1.070                   
43105                                              1.000                   

       data.ref.publication_date  \
0      2014-12-01T00:00:00+00:00   
1      2019-08-26T00:00:00+00:00   
2      2012-10-08T00:00:00+00:00   
3      2018-07-09T00:00:00+00:00   
4      2016-02-03T00:00:00+00:00   
...                          ...   
43101  2018-04-28T00:00:00+00:00   
43102  2015-07-01T00:00:00+00:00   
43103  2017-02-23T00:00:00+00:00   
43104  2017-05-02T00:00:00+00:00   
43105  2016-09-03T00:00:00+00:00   

       results.properties.electronic.band_gap[0].value  
0                                         2.563483e-19  
1                                                  NaN  
2                                         2.403265e-19  
3                                         2.563483e-19  
4                                         2.563483e-19  
...                                                ...  
43101                                     2.563483e-19  
43102                                     2.563483e-19  
43103                                     2.563483e-19  
43104                                     2.563483e-19  
43105                                     2.563483e-19  

[43106 rows x 4 columns]

In [ ]:
import re
import requests
import pandas as pd
import jmespath

# Default to staging; you can override per call
DEFAULT_URL = "https://nomad-lab.eu/prod/v1/staging/api/v1/entries/query"
INDEX_RE = re.compile(r"\[[^\]]*\]")

def normalize_quantity(q: str) -> str:
    return q.split("#", 1)[0]

def quantity_for_required(q: str) -> set[str]:
    if "#" in q:
        base, suffix = q.split("#", 1)
        suffix = f"#{suffix}"
    else:
        base, suffix = q, ""
    base = INDEX_RE.sub("", base)
    return {base + suffix}

def scalarize(val):
    if isinstance(val, (list, tuple, set)):
        return next(iter(val), None)
    return val

def dotted_get(d, path):
    cur = d
    for key in path.split("."):
        if isinstance(cur, list):
            cur = cur[0] if cur else None
        if not isinstance(cur, dict):
            return None
        cur = cur.get(key)
        if cur is None:
            return None
    return scalarize(cur)

def jmes_get(d, expr):
    try:
        return scalarize(jmespath.search(expr, d))
    except Exception:
        return dotted_get(d, expr)

def post(query, base_url: str = DEFAULT_URL, token: str | None = None):
    headers = {"Content-Type": "application/json"}
    cookies = None
    if token:
        token = str(token).strip()
        headers["Authorization"] = f"Bearer {token}"
        cookies = {"nomad_token": token}

    r = requests.post(base_url, json=query, headers=headers, cookies=cookies, timeout=60)

    if r.status_code == 422:
        try:
            payload = r.json()
        except ValueError:
            payload = r.text
        raise requests.HTTPError(
            f"422 from NOMAD. Request was rejected with: {payload}",
            response=r
        )
    r.raise_for_status()
    return r.json()

def fetch_all(base_query, base_url: str = DEFAULT_URL, token: str | None = None):
    q = {
        **base_query,
        "query": dict(base_query.get("query", {})),
        "pagination": dict(base_query.get("pagination", {})),
        "required": dict(base_query.get("required", {})),
    }
    items = []
    while True:
        resp = post(q, base_url=base_url, token=token)
        items.extend(resp.get("data", []))
        nxt = resp.get("pagination", {}).get("next_page_after_value")
        if not nxt:
            break
        q["pagination"]["page_after_value"] = nxt
    return items

def fetch_dataframe(
    quantities,
    page_size=1000,
    order="asc",
    order_by="entry_id",
    *,
    base_url: str = DEFAULT_URL,
    token: str | None = None,
):
    """
    quantities: list of NOMAD quantity paths (may contain indices and/or '#Section' suffix)
    base_url: entries/query endpoint to call (e.g. Oasis)
    token: bearer token for protected Oases (also passed as cookie)
    """
    include = sorted({inc for q in quantities for inc in quantity_for_required(q)})
    base_query = {
        "owner": "visible",
        "query": {
            "and": [
                {},
                {
                    "section_defs.definition_qualified_name:all": [
                        "perovskite_solar_cell_database.schema.PerovskiteSolarCell",
                        # "perovskite_solar_cell_database.composition.PerovskiteAIon",
                    ]
                }
            ]
        },
        "pagination": {"page_size": page_size, "order": order, "order_by": order_by},
        "required": {"include": include},
    }

    records = fetch_all(base_query, base_url=base_url, token=token)
    norm_paths = {q: normalize_quantity(q) for q in quantities}

    rows = []
    for item in records:
        row = {}
        for original_q, norm_q in norm_paths.items():
            if norm_q == "entry_id":
                row[original_q] = item.get("entry_id")
            else:
                row[original_q] = jmes_get(item, norm_q)
        rows.append(row)

    rename_cols = {q: norm_paths[q] for q in quantities}
    df = pd.DataFrame(rows).rename(columns=rename_cols)
    return df

In [ ]:
# 1) Get a token from the Oasis (adjust path if needed)
import os, getpass, requests
OASIS_BASE = "https://nomad-lab.eu/prod/v1/oasis"
OASIS_QUERY = f"{OASIS_BASE}/api/v1/entries/query"

username = os.getenv("NOMAD_USERNAME") or input("Username: ")
password = os.getenv("NOMAD_PASSWORD") or getpass.getpass("Password: ")

tok_resp = requests.post(f"{OASIS_BASE}/api/v1/auth/token",
                         data={"username": username, "password": password},
                         timeout=30)
tok_resp.raise_for_status()
TOKEN = tok_resp.json()["access_token"]

# 2) Your quantities
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "results.properties.optoelectronic.solar_cell.efficiency",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "data.ref.name_of_person_entering_the_data#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "results.properties.electronic.band_gap[0].value",
]

# 3) Pull from Oasis only
df = fetch_dataframe(
    quantities=quantities,
    page_size=2000,
)

print(df.head(), len(df))

                       entry_id  \
0  --7QgUnINWBA_TA8jw3CCbRCRrcH   
1  --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2  --9aa7m8b7HiItY8dhvSOhYziIQL   
3  --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4  --MwIi0wc7g_1YhFm95OcLR-Gp1p   

   results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                              1.000                   
1                                              0.960                   
2                                              0.632                   
3                                              0.912                   
4                                              0.885                   

   data.ref.publication_date  results.properties.electronic.band_gap[0].value  
0  2014-12-01T00:00:00+00:00                                     2.563483e-19  
1  2019-08-26T00:00:00+00:00                                              NaN  
2  2012-10-08T00:00:00+00:00                                     2.403265e-19  
3  2018-07-09T00:00:00+00:00        

In [ ]:
# 1) Get a token from the Oasis (adjust path if needed)
import os, getpass, requests
OASIS_BASE = "https://nomad-lab.eu/prod/v1/oasis"
OASIS_QUERY = f"{OASIS_BASE}/api/v1/entries/query"

username = os.getenv("NOMAD_USERNAME") or input("Username: ")
password = os.getenv("NOMAD_PASSWORD") or getpass.getpass("Password: ")

tok_resp = requests.post(f"{OASIS_BASE}/api/v1/auth/token",
                         data={"username": username, "password": password},
                         timeout=30)
tok_resp.raise_for_status()
TOKEN = tok_resp.json()["access_token"]

# 2) Your quantities
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "results.properties.optoelectronic.solar_cell.efficiency",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "data.ref.name_of_person_entering_the_data#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "results.properties.electronic.band_gap[0].value",
]

# 3) Pull from Oasis only
df_llm = fetch_dataframe(
    quantities=quantities,
    page_size=2000,
    base_url=OASIS_QUERY,
    token=TOKEN,
)

print(df_llm.head(), len(df_llm))

                       entry_id  \
0  --7QgUnINWBA_TA8jw3CCbRCRrcH   
1  --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2  --9aa7m8b7HiItY8dhvSOhYziIQL   
3  --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4  --MwIi0wc7g_1YhFm95OcLR-Gp1p   

   results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                              1.000                   
1                                              0.960                   
2                                              0.632                   
3                                              0.912                   
4                                              0.885                   

   data.ref.publication_date  results.properties.electronic.band_gap[0].value  
0  2014-12-01T00:00:00+00:00                                     2.563483e-19  
1  2019-08-26T00:00:00+00:00                                              NaN  
2  2012-10-08T00:00:00+00:00                                     2.403265e-19  
3  2018-07-09T00:00:00+00:00        

In [132]:
# merge df and df_llm
df = pd.concat([df, df_llm]).drop_duplicates().reset_index(drop=True)
print(df.head(), len(df))

                       entry_id  \
0  --7QgUnINWBA_TA8jw3CCbRCRrcH   
1  --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2  --9aa7m8b7HiItY8dhvSOhYziIQL   
3  --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4  --MwIi0wc7g_1YhFm95OcLR-Gp1p   

   results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                              1.000                   
1                                              0.960                   
2                                              0.632                   
3                                              0.912                   
4                                              0.885                   

   data.ref.publication_date  results.properties.electronic.band_gap[0].value  
0  2014-12-01T00:00:00+00:00                                     2.563483e-19  
1  2019-08-26T00:00:00+00:00                                              NaN  
2  2012-10-08T00:00:00+00:00                                     2.403265e-19  
3  2018-07-09T00:00:00+00:00        

In [133]:
# change bandgap values to eV 
df["results.properties.electronic.band_gap[0].value"] = df["results.properties.electronic.band_gap[0].value"].apply(lambda x: x / 1.60218e-19 if pd.notnull(x) else x)
df

entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
1      --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2      --9aa7m8b7HiItY8dhvSOhYziIQL   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
...                             ...   
51183  zyV4owfuF0QaTrOanxqooskLc07f   
51184  zz3SeGApJE2tgQ5UXJf8G2xw1BSH   
51185  zz9fFxnTd6UlGHJOuDHp3zeQhmP6   
51186  zzHxs1g8bIkDsf7Vp8DGRZo3DIOR   
51187  zzUkAiOz0hz3r3DeNhtFSp9CqHGz   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
1                                                  0.960                   
2                                                  0.632                   
3                                                  0.912                   
4                                                  0.885                   
...                                                  ...                   
51183                                              1.030                   
51184                                              1.086                   
51185                                              1.170                   
51186                                                NaN                   
51187                                              1.149                   

       data.ref.publication_date  \
0      2014-12-01T00:00:00+00:00   
1      2019-08-26T00:00:00+00:00   
2      2012-10-08T00:00:00+00:00   
3      2018-07-09T00:00:00+00:00   
4      2016-02-03T00:00:00+00:00   
...                          ...   
51183  2024-03-04T11:31:24+00:00   
51184  2024-06-05T10:47:27+00:00   
51185  2025-02-16T16:09:36+00:00   
51186  2022-09-19T16:11:53+00:00   
51187  2024-12-17T08:37:53+00:00   

       results.properties.electronic.band_gap[0].value  
0                                             1.599997  
1                                                  NaN  
2                                             1.499997  
3                                             1.599997  
4                                             1.599997  
...                                                ...  
51183                                         1.549997  
51184                                         1.549997  
51185                                         1.499997  
51186                                         1.599997  
51187                                              NaN  

[51188 rows x 4 columns]

In [135]:
#  lets caluclate the sqvoc we can use this qVSQOC = -0.167 + 0.932*Eg

df["sqvoc"] = -0.167 + 0.932 * df["results.properties.electronic.band_gap[0].value"]
df

entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
1      --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2      --9aa7m8b7HiItY8dhvSOhYziIQL   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
...                             ...   
51183  zyV4owfuF0QaTrOanxqooskLc07f   
51184  zz3SeGApJE2tgQ5UXJf8G2xw1BSH   
51185  zz9fFxnTd6UlGHJOuDHp3zeQhmP6   
51186  zzHxs1g8bIkDsf7Vp8DGRZo3DIOR   
51187  zzUkAiOz0hz3r3DeNhtFSp9CqHGz   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
1                                                  0.960                   
2                                                  0.632                   
3                                                  0.912                   
4                                                  0.885                   
...                                                  ...                   
51183                                              1.030                   
51184                                              1.086                   
51185                                              1.170                   
51186                                                NaN                   
51187                                              1.149                   

       data.ref.publication_date  \
0      2014-12-01T00:00:00+00:00   
1      2019-08-26T00:00:00+00:00   
2      2012-10-08T00:00:00+00:00   
3      2018-07-09T00:00:00+00:00   
4      2016-02-03T00:00:00+00:00   
...                          ...   
51183  2024-03-04T11:31:24+00:00   
51184  2024-06-05T10:47:27+00:00   
51185  2025-02-16T16:09:36+00:00   
51186  2022-09-19T16:11:53+00:00   
51187  2024-12-17T08:37:53+00:00   

       results.properties.electronic.band_gap[0].value     sqvoc  
0                                             1.599997  1.324197  
1                                                  NaN       NaN  
2                                             1.499997  1.230997  
3                                             1.599997  1.324197  
4                                             1.599997  1.324197  
...                                                ...       ...  
51183                                         1.549997  1.277597  
51184                                         1.549997  1.277597  
51185                                         1.499997  1.230997  
51186                                         1.599997  1.324197  
51187                                              NaN       NaN  

[51188 rows x 5 columns]

In [ ]:
# let's drop rows with missing values in any of the relevant columns
df.dropna(subset=['results.properties.optoelectronic.solar_cell.open_circuit_voltage', 'data.ref.publication_date', 'results.properties.electronic.band_gap[0].value', 'sqvoc'], inplace=True)

# remove rows where the diff is negative
df = df[df['results.properties.optoelectronic.solar_cell.open_circuit_voltage'] <= df['sqvoc']]
df

entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
5      --Phx81KXd8q_-bTnwpZPUIWWiVa   
6      --RgE_khB0mtMTpdsdxLae7XuLI0   
...                             ...   
51181  zy2cV7Iqjqg0UmsM8BL_Z6-gavUR   
51182  zyFvrBw4rSmI32dnzpz9HpQewN1u   
51183  zyV4owfuF0QaTrOanxqooskLc07f   
51184  zz3SeGApJE2tgQ5UXJf8G2xw1BSH   
51185  zz9fFxnTd6UlGHJOuDHp3zeQhmP6   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
3                                                  0.912                   
4                                                  0.885                   
5                                                  0.980                   
6                                                  1.040                   
...                                                  ...                   
51181                                              1.220                   
51182                                              1.220                   
51183                                              1.030                   
51184                                              1.086                   
51185                                              1.170                   

       data.ref.publication_date  \
0      2014-12-01T00:00:00+00:00   
3      2018-07-09T00:00:00+00:00   
4      2016-02-03T00:00:00+00:00   
5      2019-04-10T00:00:00+00:00   
6      2018-05-02T00:00:00+00:00   
...                          ...   
51181  2023-05-26T20:00:05+00:00   
51182  2024-11-13T14:14:56+00:00   
51183  2024-03-04T11:31:24+00:00   
51184  2024-06-05T10:47:27+00:00   
51185  2025-02-16T16:09:36+00:00   

       results.properties.electronic.band_gap[0].value     sqvoc      diff  
0                                             1.599997  1.324197  0.324197  
3                                             1.599997  1.324197  0.412197  
4                                             1.599997  1.324197  0.439197  
5                                             1.599997  1.324197  0.344197  
6                                             1.599997  1.324197  0.284197  
...                                                ...       ...       ...  
51181                                         1.717996  1.434173  0.214173  
51182                                         1.649997  1.370797  0.150797  
51183                                         1.549997  1.277597  0.247597  
51184                                         1.549997  1.277597  0.191597  
51185                                         1.499997  1.230997  0.060997  

[37102 rows x 6 columns]

In [150]:
# lets get some statistic of the yearly reported values for the sqvoc - voc, do the difference per row first and then do the stats

df["diff"] = df["sqvoc"] - df["results.properties.optoelectronic.solar_cell.open_circuit_voltage"]

# lets get now the stats per year

df.groupby(df["data.ref.publication_date"].str[:4])["diff"].describe()

# exclude data bafore 2013

df = df[df["data.ref.publication_date"].str[:4].astype(int) >= 2013]

# lets plot the mean and std dev per year with plotly 

import plotly.express as px
fig = px.scatter(df.groupby(df["data.ref.publication_date"].str[:4])["diff"].describe().reset_index(), x="data.ref.publication_date", y="mean", error_y="std", labels={"data.ref.publication_date": "Year", "mean": "Mean of <i>V</i><sub>SQ</sub> − <i>V</i><sub>OC</sub>", "std": "Standard Deviation"})
fig.update_layout(
    yaxis_title="Yearly mean of <i>V</i><sub>SQ</sub> − <i>V</i><sub>OC</sub>"
)

fig.update_traces(mode='markers', marker_line_width=0.5, marker_size=12)

# add a red fitted line to the plot and label the average decay per year. Do the fit first

import numpy as np
from scipy import stats

x = df.groupby(df["data.ref.publication_date"].str[:4])["diff"].describe().reset_index()["data.ref.publication_date"].astype(int)
y = df.groupby(df["data.ref.publication_date"].str[:4])["diff"].describe().reset_index()["mean"]

slope, intercept, r_value, p_value, std_err = stats.linregress(x, y)
print(f"Slope: {slope}, Intercept: {intercept}, R-squared: {r_value**2}")

fig.add_traces(px.line(x=x, y=intercept + slope * x, labels={"x": "Year", "y": "Fitted line"}).update_traces(line_color='red').data)

fig.show()




Slope: -0.021424418644516396, Intercept: 43.6069191117957, R-squared: 0.9668594586873976


In [151]:
# exclude data before 2013

df = df[df["data.ref.publication_date"].str[:4].astype(int) >= 2013]

# let's do it now with a box plot and lets also plot the scater values form the big df with very very low opacity. Not sue what is the best way to aproach it. overlaying a scatter plot for this?

import plotly.express as px
fig = px.violin(df, x=df["data.ref.publication_date"].str[:4], y="diff", box=True, points="all",  labels={"x": "Year", "diff": "<i>V</i><sub>OC</sub><sup>SQ</sup> − <i>V</i><sub>OC</sub>"})
fig.update_traces(marker=dict(opacity=0.1))

# add a fitted trend line in red
import numpy as np
import plotly.graph_objects as go

years = df["data.ref.publication_date"].str[:4].astype(int).unique()
years.sort()
mean_diff = df.groupby(df["data.ref.publication_date"].str[:4])["diff"].mean().reindex(years.astype(str)).values
meadian_diff = df.groupby(df["data.ref.publication_date"].str[:4])["diff"].median().reindex(years.astype(str)).values
# Fit a linear trend line
coeffs = np.polyfit(years, meadian_diff, 1)
trend_line = np.polyval(coeffs, years)

#calculate the slope and intercept
slope = coeffs[0]
intercept = coeffs[1]

# print r-squared value
correlation_matrix = np.corrcoef(years, meadian_diff)
correlation_xy = correlation_matrix[0,1]
r_squared = correlation_xy**2
print(f"R-squared: {r_squared}")

fig.add_trace(go.Scatter(x=years, y=trend_line, mode='lines', line=dict(color='red'), name=f'{slope:.3f} V / year'))
fig.show()


R-squared: 0.9741339901378612


In [19]:
# --- Example usage ---
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
]

df = fetch_dataframe(
    quantities=quantities,
    page_size=10000
)

df

KeyboardInterrupt: 

In [50]:
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    "results.properties.electronic.band_gap[0].value"
]

df_llm = fetch_dataframe(
    quantities=quantities,
    page_size=10000
)

df_llm

HTTPError: 422 Client Error: Unprocessable Entity for url: https://nomad-lab.eu/prod/v1/oasis/api/v1/entries/query

In [3]:
import plotly.express as px

fig = px.scatter(
    df.dropna(subset=['results.properties.optoelectronic.solar_cell.open_circuit_voltage', 'data.ref.publication_date']),
    x='data.ref.publication_date',
    y='results.properties.optoelectronic.solar_cell.open_circuit_voltage',
    labels={
        'data.ref.publication_date': 'Publication Date',
        'results.properties.optoelectronic.solar_cell.open_circuit_voltage': 'Open-circuit voltage (V)'
    }
)
fig

In [54]:
df.dropna(subset=['results.properties.optoelectronic.solar_cell.open_circuit_voltage', 'data.ref.publication_date'])


entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
1      --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2      --9aa7m8b7HiItY8dhvSOhYziIQL   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
...                             ...   
43101  zzWmvvMCjbgxrnv6lvDISU7jQnDJ   
43102  zzZw_wGNpfUjQTtHnuNTSLZ_qG8s   
43103  zzdMGwagDZsgwpm8rCyYpDBkdOnR   
43104  zzo4cqAqKXO34NtM9ZItcLbh302O   
43105  zzsi9PLwayzu6t_th5OYrfmZsCIJ   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
1                                                  0.960                   
2                                                  0.632                   
3                                                  0.912                   
4                                                  0.885                   
...                                                  ...                   
43101                                              0.970                   
43102                                              0.981                   
43103                                              0.910                   
43104                                              1.070                   
43105                                              1.000                   

       data.ref.publication_date results.properties.electronic.band_gap.value  
0      2014-12-01T00:00:00+00:00                                         None  
1      2019-08-26T00:00:00+00:00                                         None  
2      2012-10-08T00:00:00+00:00                                         None  
3      2018-07-09T00:00:00+00:00                                         None  
4      2016-02-03T00:00:00+00:00                                         None  
...                          ...                                          ...  
43101  2018-04-28T00:00:00+00:00                                         None  
43102  2015-07-01T00:00:00+00:00                                         None  
43103  2017-02-23T00:00:00+00:00                                         None  
43104  2017-05-02T00:00:00+00:00                                         None  
43105  2016-09-03T00:00:00+00:00                                         None  

[40918 rows x 4 columns]

In [10]:
from pepe_plotly_theme import register_template, scatter_plot

register_template()

fig = scatter_plot(
    x=df['data.ref.publication_date'],
    y=df['results.properties.optoelectronic.solar_cell.open_circuit_voltage'],
    x_title = 'Publication date',
    y_title = 'Open circuit voltage (V)',
    opacity = 0.7,
    y_nticks = 6
    )

fig

fig.update_traces(mode='markers', marker_line_width=0.5, marker_size=10)

fig.show()

In [6]:
import os, sys
print(os.getcwd())                 # notebook’s working dir
print(os.listdir())                # should list your .py file
# If needed:
sys.path.append(os.path.abspath("."))  # ensure current folder is importable

/Users/pepemarquez/git/Pepe-Marquez/nomad-distro-dev/packages/nomad-perovskite-solar-cells-database/src/perovskite_solar_cell_database/example_uploads/perovskite_database
['crabnet-perovskite-bandgap-prediction.ipynb', 'perovskite-data-analysis.ipynb', '__init__.py', '__pycache__', 'pepe_plotly_theme.py']


In [12]:
df.describe()

results.properties.optoelectronic.solar_cell.open_circuit_voltage
count                                       40918.000000                
mean                                            0.962211                
std                                             0.183881                
min                                             0.000000                
25%                                             0.900000                
50%                                             1.000000                
75%                                             1.070000                
max                                             4.050000

In [ ]:
# Optional: keep rows with both values for plotting
cols_for_plot = [
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.pure_substance.molar_mass#perovskite_solar_cell_database.composition.PerovskiteAIon",
]
df_plot = df.dropna(subset=cols_for_plot)

print(df.head())
print(f"Total rows: {len(df)}; rows with both plot fields: {len(df_plot)}")

# Example plot
import matplotlib.pyplot as plt
ax = df_plot.plot.scatter(
    x="data.pure_substance.molar_mass#perovskite_solar_cell_database.composition.PerovskiteAIon",
    y="results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    title="Voc vs A-site molar mass"
)
ax.set_xlabel("A-site molar mass (g/mol)")
ax.set_ylabel("Open-circuit voltage (V)")
plt.show()

In [15]:
import plotly.graph_objects as go
import numpy as np


t = np.linspace(0, 10, 100)

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=t, y=np.sin(t),
    name='sin',
    mode='markers',
    marker_color='rgba(152, 0, 0, .8)'
))

fig.add_trace(go.Scatter(
    x=t, y=np.cos(t),
    name='cos',
    marker_color='rgba(255, 182, 193, .3)'
))

# Set options common to all traces with fig.update_traces
fig.update_traces(mode='markers', marker_line_width=2, marker_size=10)
fig.update_layout(
                  yaxis_zeroline=False, xaxis_zeroline=False)


fig.show()

In [46]:
import requests
import pandas as pd

try:
    import jmespath
except ImportError:
    jmespath = None


# ---------- helpers ----------
def normalize_quantity(q: str) -> str:
    """NOMAD 'required.include' may have a '#Section' suffix; API payload keys don't."""
    return q.split("#", 1)[0]

def scalarize(val):
    if isinstance(val, (list, tuple, set)):
        return next(iter(val), None)
    return val

def dotted_get(d, path):
    cur = d
    for key in path.split("."):
        if isinstance(cur, list):
            cur = cur[0] if cur else None
        if not isinstance(cur, dict):
            return None
        cur = cur.get(key)
        if cur is None:
            return None
    return scalarize(cur)

def jmes_get(d, expr):
    if jmespath:
        try:
            return scalarize(jmespath.search(expr, d))
        except Exception:
            return dotted_get(d, expr)
    return dotted_get(d, expr)


# ---------- core client ----------
class NomadClient:
    def __init__(self, base_url: str, api_token: str | None = None, timeout: int = 60):
        """
        base_url: e.g. 'https://nomad-lab.eu/prod/v1/staging'
                  or an Oasis base like 'https://<your-oasis>/api'
        We'll append '/api/v1/entries/query' if you pass a root-like URL.
        """
        base = base_url.rstrip("/")
        if not base.endswith("/api") and not base.endswith("/api/v1") and not base.endswith("/api/v1/entries/query"):
            # assume a NOMAD root; stitch the standard path
            self.query_url = f"{base}/api/v1/entries/query"
        elif base.endswith("/api"):
            self.query_url = f"{base}/v1/entries/query"
        elif base.endswith("/api/v1"):
            self.query_url = f"{base}/entries/query"
        else:  # already the exact endpoint
            self.query_url = base

        self.session = requests.Session()
        self.session.headers.update({"Content-Type": "application/json"})
        # if api_token:
        #     self.session.headers.update({"Authorization": f"Bearer {api_token}"})
        # self.timeout = timeout
# --- add this inside NomadClient.__init__ right after setting headers ---
# inside NomadClient.__init__
        if api_token:
            api_token = str(api_token).strip()
            self.session.headers.update({"Authorization": f"Bearer {api_token}"})
            self.session.cookies.set("nomad_token", api_token)  # <- no domain kwarg
        self.timeout = timeout

        # --- add this method to NomadClient ---
    def verify_auth(self) -> dict:
        """
        Returns a dict like {"ok": True/False, "owner": "...", "sample_count": N}
        If ok=True and owner=='user', your token is being honored.
        """
        try:
            resp = self.post({
                "query": {},
                "owner": "user",                    # <-- ask for user-owned scope
                "pagination": {"page_size": 1},     # small, just to test
                "required": {"include": ["entry_id"]}
            })
            owner = resp.get("owner")
            return {"ok": owner == "user", "owner": owner, "sample_count": len(resp.get("data", []))}
        except requests.HTTPError as e:
            return {"ok": False, "error": f"{e.response.status_code} {e.response.text[:200]}"}

    def post(self, query: dict) -> dict:
        r = self.session.post(self.query_url, json=query, timeout=self.timeout)
        r.raise_for_status()
        return r.json()

    def fetch_all(self, base_query: dict) -> list[dict]:
        """Paginates until no next_page_after_value."""
        # Deep-ish copy of key sections to avoid mutating caller input
        q = {
            **base_query,
            "query": dict(base_query.get("query", {})),
            "pagination": dict(base_query.get("pagination", {})),
            "required": dict(base_query.get("required", {})),
        }
        items = []
        while True:
            resp = self.post(q)
            items.extend(resp.get("data", []))
            nxt = resp.get("pagination", {}).get("next_page_after_value")
            if not nxt:
                break
            q["pagination"]["page_after_value"] = nxt
        return items

    def fetch_dataframe(
        self,
        quantities: list[str],
        base_query: dict,
        source_label: str | None = None,
    ) -> pd.DataFrame:
        """
        quantities: list of NOMAD quantity paths (may include '#Section' suffix)
        base_query: full query dict ('query', 'required', 'pagination' etc.)
        source_label: optional string to tag rows with the origin (e.g. URL or nickname)
        """
        # Ensure required.include contains the requested quantities as provided
        q = {
            **base_query,
            "required": {
                **base_query.get("required", {}),
                "include": list({*(base_query.get("required", {}).get("include", [])), *quantities}),
            },
        }
        records = self.fetch_all(q)

        # Extract rows
        norm_paths = {q: normalize_quantity(q) for q in quantities}
        rows = []
        for item in records:
            row = {}
            for original_q, norm_q in norm_paths.items():
                if norm_q == "entry_id":
                    row[original_q] = item.get("entry_id")
                else:
                    row[original_q] = jmes_get(item, norm_q)
            if source_label is not None:
                row["_source"] = source_label
            rows.append(row)

        # Normalize column headers (drop '#Section' suffix)
        rename_cols = {q: norm_paths[q] for q in quantities}
        df = pd.DataFrame(rows).rename(columns=rename_cols)
        return df


# ---------- convenience: multi-host fetch ----------
def fetch_from_multiple(
    urls: list[str] | dict[str, str],
    quantities: list[str],
    base_query: dict,
    per_url_overrides: dict[str, dict] | None = None,
    tokens: dict[str, str] | None = None,
) -> pd.DataFrame:
    """
    urls: list of base URLs OR dict of {label: base_url}
    quantities: same quantities applied to all
    base_query: default query applied to all
    per_url_overrides: optional dict {label_or_url: {query/pagination/required...}}
    tokens: optional dict {label_or_url: bearer_token}
    """
    frames = []

    if isinstance(urls, dict):
        items = list(urls.items())  # (label, url)
    else:
        items = [(u, u) for u in urls]  # label == url

    for label, url in items:
        token = (tokens or {}).get(label) or (tokens or {}).get(url)
        client = NomadClient(url, api_token=token)

        # merge base_query with per-url overrides (shallow merge of top-level keys)
        q = dict(base_query)
        if per_url_overrides and (label in per_url_overrides or url in per_url_overrides):
            override = per_url_overrides.get(label) or per_url_overrides.get(url)
            q = {
                **q,
                **override,
                "query": {**q.get("query", {}), **override.get("query", {})},
                "pagination": {**q.get("pagination", {}), **override.get("pagination", {})},
                "required": {**q.get("required", {}), **override.get("required", {})},
            }

        df = client.fetch_dataframe(
            quantities=quantities,
            base_query=q,
            source_label=label,
        )
        frames.append(df)

    if not frames:
        return pd.DataFrame(columns=[*(normalize_quantity(q) for q in quantities), "_source"])

    # Align columns and concat
    out = pd.concat(frames, ignore_index=True, sort=False)
    return out


# ---------- example usage ----------
# Your base quantities
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
]

# Default query used for every host unless overridden
default_query = {
    "query": {
        "and": [
            {
                "section_defs.definition_qualified_name:all": [
                    "perovskite_solar_cell_database.schema.PerovskiteSolarCell",
                ]
            }
        ]
    },
    "pagination": {"page_size": 10_000, "order": "asc", "order_by": "entry_id"},
    "required": {"include": []},  # will be merged with 'quantities'
}

# Multiple installations (labels are nice for the _source column)
hosts = {
    "Example-Oasis": "https://nomad-lab.eu/prod/v1/oasis",
    "NOMAD-prod-staging": "https://nomad-lab.eu/prod/v1/staging",

}

# Optional: per-host tweaks (e.g., different section names, smaller page_size, etc.)
overrides = {
    # "Example-Oasis": {
    #     "query": {
    #         "and": [
    #         {
    #             "section_defs.definition_qualified_name:all": [
    #                 "perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    #             ]
    #         }
    #         ]
    #     },
    #     "pagination": {"page_size": 5000},
    # }
}

# Optional: auth tokens if any host requires it
import os, getpass

username = os.getenv('NOMAD_USERNAME') or input('Username: ')
password = os.getenv('NOMAD_PASSWORD') or getpass.getpass('Password: ')

response_token = requests.post(
    f"{hosts['Example-Oasis']}/api/v1/auth/token",
    data={'username': username, 'password': password},
)
token = response_token.json()['access_token']

tokens = {
    "Example-Oasis": token,
}

df = fetch_from_multiple(
    urls=hosts,
    quantities=quantities,
    base_query=default_query,
    per_url_overrides=overrides,
    tokens=tokens,
)

# Peek
print(df.head())

                       entry_id  \
0  --7QgUnINWBA_TA8jw3CCbRCRrcH   
1  --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2  --9aa7m8b7HiItY8dhvSOhYziIQL   
3  --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4  --MwIi0wc7g_1YhFm95OcLR-Gp1p   

   results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                              1.000                   
1                                              0.960                   
2                                              0.632                   
3                                              0.912                   
4                                              0.885                   

   data.ref.publication_date             _source  
0  2014-12-01T00:00:00+00:00  NOMAD-prod-staging  
1  2019-08-26T00:00:00+00:00  NOMAD-prod-staging  
2  2012-10-08T00:00:00+00:00  NOMAD-prod-staging  
3  2018-07-09T00:00:00+00:00  NOMAD-prod-staging  
4  2016-02-03T00:00:00+00:00  NOMAD-prod-staging  


In [47]:
df

entry_id  \
0      --7QgUnINWBA_TA8jw3CCbRCRrcH   
1      --8F7Y4s3uKDX5NP3bucanTkQo8Q   
2      --9aa7m8b7HiItY8dhvSOhYziIQL   
3      --MlWiNv1SKTzJtpJWHqwwxmmsDW   
4      --MwIi0wc7g_1YhFm95OcLR-Gp1p   
...                             ...   
43101  zzWmvvMCjbgxrnv6lvDISU7jQnDJ   
43102  zzZw_wGNpfUjQTtHnuNTSLZ_qG8s   
43103  zzdMGwagDZsgwpm8rCyYpDBkdOnR   
43104  zzo4cqAqKXO34NtM9ZItcLbh302O   
43105  zzsi9PLwayzu6t_th5OYrfmZsCIJ   

       results.properties.optoelectronic.solar_cell.open_circuit_voltage  \
0                                                  1.000                   
1                                                  0.960                   
2                                                  0.632                   
3                                                  0.912                   
4                                                  0.885                   
...                                                  ...                   
43101                                              0.970                   
43102                                              0.981                   
43103                                              0.910                   
43104                                              1.070                   
43105                                              1.000                   

       data.ref.publication_date             _source  
0      2014-12-01T00:00:00+00:00  NOMAD-prod-staging  
1      2019-08-26T00:00:00+00:00  NOMAD-prod-staging  
2      2012-10-08T00:00:00+00:00  NOMAD-prod-staging  
3      2018-07-09T00:00:00+00:00  NOMAD-prod-staging  
4      2016-02-03T00:00:00+00:00  NOMAD-prod-staging  
...                          ...                 ...  
43101  2018-04-28T00:00:00+00:00  NOMAD-prod-staging  
43102  2015-07-01T00:00:00+00:00  NOMAD-prod-staging  
43103  2017-02-23T00:00:00+00:00  NOMAD-prod-staging  
43104  2017-05-02T00:00:00+00:00  NOMAD-prod-staging  
43105  2016-09-03T00:00:00+00:00  NOMAD-prod-staging  

[43106 rows x 4 columns]

In [45]:
client = NomadClient(hosts["Example-Oasis"], api_token=tokens["Example-Oasis"])
print("Query URL:", client.query_url)
print("Auth:", client.verify_auth())  # expect {'ok': True, 'owner': 'user'}

Query URL: https://nomad-lab.eu/prod/v1/oasis/api/v1/entries/query
Auth: {'ok': True, 'owner': 'user', 'sample_count': 1}


In [30]:
hosts['Example-Oasis']

'https://nomad-lab.eu/prod/v1/oasis'

In [38]:
# 0) Build client with both header+cookie token
oasis = hosts["Example-Oasis"]
client = NomadClient(oasis, api_token=tokens["Example-Oasis"])
client.session.cookies.set("nomad_token", tokens["Example-Oasis"])
print("Query URL:", client.query_url)

# 1) No-filter query for entry_id
test = {"query": {}, "pagination": {"page_size": 3}, "required": {"include": ["entry_id"]}}
print(client.post(test))

# 2) If (1) returns rows, now try your real quantities WITHOUT the section filter:
test2 = {
    "query": {},
    "pagination": {"page_size": 50},
    "required": {"include": [
        "entry_id",
        "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
        "data.ref.publication_date#perovskite_solar_cell_database.schema.PerovskiteSolarCell",
    ]},
}
print("Rows with your includes (no section filter):", len(client.post(test2).get("data", [])))

# 3) Discover what section defs exist, then adjust your filter accordingly.

Query URL: https://nomad-lab.eu/prod/v1/oasis/api/v1/entries/query
{'owner': 'public', 'query': {'and': []}, 'pagination': {'page_size': 3, 'order_by': 'entry_id', 'order': 'asc', 'total': 52, 'next_page_after_value': '3xb929weZhHOjsswxx9zMu2VL7RX'}, 'required': {'include': ['entry_id']}, 'data': [{'entry_id': '3BFqAsfbKx_GN-83K25Es3Br59eC'}, {'entry_id': '3HqsyNFUgLz9KdmPOY-RiElEMI9e'}, {'entry_id': '3xb929weZhHOjsswxx9zMu2VL7RX'}]}
Rows with your includes (no section filter): 50


In [48]:
import requests
import pandas as pd

try:
    import jmespath
except ImportError:
    jmespath = None

# -------- minimal helpers --------
def normalize_quantity(q: str) -> str:
    return q.split("#", 1)[0]

def scalarize(v):
    if isinstance(v, (list, tuple, set)):
        return next(iter(v), None)
    return v

def dotted_get(d, path):
    cur = d
    for k in path.split("."):
        if isinstance(cur, list):
            cur = cur[0] if cur else None
        if not isinstance(cur, dict):
            return None
        cur = cur.get(k)
        if cur is None:
            return None
    return scalarize(cur)

def jmes_get(d, expr):
    if jmespath:
        try:
            return scalarize(jmespath.search(expr, d))
        except Exception:
            return dotted_get(d, expr)
    return dotted_get(d, expr)

# -------- tiny Oasis-only client --------
class NomadClient:
    def __init__(self, base_url: str, api_token: str | None = None, timeout: int = 60):
        base = base_url.rstrip("/")
        if not base.endswith("/api") and not base.endswith("/api/v1") and not base.endswith("/api/v1/entries/query"):
            self.query_url = f"{base}/api/v1/entries/query"
        elif base.endswith("/api"):
            self.query_url = f"{base}/v1/entries/query"
        elif base.endswith("/api/v1"):
            self.query_url = f"{base}/entries/query"
        else:
            self.query_url = base

        self.session = requests.Session()
        self.session.headers.update({"Content-Type": "application/json"})
        if api_token:
            api_token = str(api_token).strip()
            self.session.headers.update({"Authorization": f"Bearer {api_token}"})
            # some Oases require the cookie form
            self.session.cookies.set("nomad_token", api_token)

        self.timeout = timeout

    def post(self, query: dict) -> dict:
        r = self.session.post(self.query_url, json=query, timeout=self.timeout)
        r.raise_for_status()
        return r.json()

    def verify_auth(self) -> dict:
        """Expect owner=='user' if token is honored."""
        resp = self.post({
            "owner": "user",
            "query": {},
            "pagination": {"page_size": 1},
            "required": {"include": ["entry_id"]},
        })
        return {"ok": resp.get("owner") == "user", "owner": resp.get("owner")}

# ---------- run a minimal Oasis-only check ----------
OASIS = "https://nomad-lab.eu/prod/v1/oasis"

# Get token from the Oasis (adjust path if your Oasis uses /auth/token without /api/v1)
import os, getpass
username = os.getenv("NOMAD_USERNAME") or input("Username: ")
password = os.getenv("NOMAD_PASSWORD") or getpass.getpass("Password: ")

token_resp = requests.post(
    f"{OASIS}/api/v1/auth/token",
    data={"username": username, "password": password},
    timeout=30,
)
token_resp.raise_for_status()
token = token_resp.json()["access_token"]

client = NomadClient(OASIS, api_token=token)
print("Query URL:", client.query_url)

# 1) Prove token is honored
print("Auth check:", client.verify_auth())  # expect {'ok': True, 'owner': 'user'}

# 2) Pull a few rows with zero filters (public+user scope)
smoke = client.post({
    "query": {},
    "pagination": {"page_size": 5},
    "required": {"include": ["entry_id", "results.material.elements"]},
})
print("Smoke rows:", len(smoke.get("data", [])))
for row in smoke.get("data", []):
    print(row.get("entry_id"), row.get("results", {}).get("material", {}).get("elements"))

# 3) List which section defs exist (sample) — helps choose the right filter later
peek = client.post({
    "query": {},
    "pagination": {"page_size": 100},
    "required": {"include": ["section_defs.definition_qualified_name"]},
})
defs = set()
for it in peek.get("data", []):
    defs.update(it.get("section_defs", {}).get("definition_qualified_name") or [])
print("Sample section defs:")
for d in sorted(defs)[:30]:
    print(" -", d)

# 4) Pull your quantities without a section filter (to confirm fields resolve)
quantities = [
    "entry_id",
    "results.properties.optoelectronic.solar_cell.open_circuit_voltage",
    "data.ref.publication_date",  # <- no '#Section' suffix for now
]

simple = client.post({
    "query": {},
    "pagination": {"page_size": 20},
    "required": {"include": quantities},
})
rows = []
for item in simple.get("data", []):
    rows.append({
        "entry_id": item.get("entry_id"),
        "results.properties.optoelectronic.solar_cell.open_circuit_voltage":
            jmes_get(item, "results.properties.optoelectronic.solar_cell.open_circuit_voltage"),
        "data.ref.publication_date":
            jmes_get(item, "data.ref.publication_date"),
    })
df = pd.DataFrame(rows)
print(df.head())

Query URL: https://nomad-lab.eu/prod/v1/oasis/api/v1/entries/query
Auth check: {'ok': True, 'owner': 'user'}
Smoke rows: 5
3BFqAsfbKx_GN-83K25Es3Br59eC []
3HqsyNFUgLz9KdmPOY-RiElEMI9e None
3xb929weZhHOjsswxx9zMu2VL7RX None
4GbwP3a_7XbG1-C3hiHEF60M6asY []
5DvWcMGxpWEKvTEkMWu467-tLMlv None


AttributeError: 'list' object has no attribute 'get'